# KLayout DRC plugin quickstart

This module provides integration between [Tidy3D](https://docs.flexcompute.com/projects/tidy3d/en/latest/) and [KLayout](https://www.klayout.de)'s [Design Rule Check (DRC) engine](https://www.klayout.de/doc/manual/drc.html), allowing you to perform design rule checks on GDS files and Tidy3D objects.

## Features

- Run DRC on GDS files or Tidy3D objects ([Geometry](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Geometry.html), [Structure](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Structure.html#tidy3d.Structure), or [Simulation](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Simulation.html#tidy3d.Simulation)) with [DRCRunner.run()](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCRunner.run).
- Load DRC results into a [DRCResults](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults) data structure with [DRCResults.load()](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults).

## Prerequisites:

1. Have the full KLayout application [installed](https://www.klayout.de/build.html) and added to your system PATH.
2. Provide a KLayout DRC [runset script](https://www.klayout.de/doc/manual/drc_runsets.html). A simple example script is included with this notebook.

Please see the [README](https://github.com/flexcompute/tidy3d/blob/develop/tidy3d/plugins/klayout/drc/README.md) for more information.

### Imports:

In [1]:
from pathlib import Path

import tidy3d as td
from tidy3d.plugins.klayout.drc import DRCResults, DRCRunner

td.config.logging.level = "INFO"

## Running DRC

To run DRC, create an instance of [DRCRunner](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCRunner) and use [DRCRunner.run()](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCRunner.run).

We can run DRC on a GDS layout file, or a Tidy3D [Geometry](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Geometry.html), [Structure](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Structure.html#tidy3d.Structure), or [Simulation](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Simulation.html#tidy3d.Simulation). In the case of a Tidy3D [Geometry](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Geometry.html), [Structure](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Structure.html#tidy3d.Structure), or [Simulation](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.Simulation.html#tidy3d.Simulation), the Tidy3D object will first be exported to a GDS file and then DRC will be ran on the exported file.

The rules and operations to run are defined in a separate runset file, following the KLayout runset syntax. A simple example runset is included. Please refer to (the KLayout documentation) for more information.

Here is a quick example of running DRC on a [PolySlab](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.PolySlab.html#tidy3d.PolySlab):

In [2]:
# Create a simply polyslab geometry
vertices = [(-2, 0), (-1, 1), (0, 0.5), (1, 1), (2, 0), (0, -1)]
geom = td.PolySlab(vertices=vertices, slab_bounds=(0, 0.22), axis=2)

# Run DRC
runner = DRCRunner(drc_runset=Path("misc") / "drc_runset.drc", verbose=True)
results = runner.run(source=geom, z=0.1, gds_layer=0, gds_dtype=0)

12:28:40 EDT INFO: Writing Tidy3D object to GDS file 'layout.gds'.

             INFO: Running KLayout DRC on GDS file 'layout.gds' with runset     
             'misc/drc_runset.drc' and saving results to 'drc_results.lyrdb'...

12:28:43 EDT INFO: KLayout DRC completed successfully.

## Loading Results

The output is a [DRCResults](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults) object that contains the DRC rules and markers. The user can check if DRC passed with [DRCResults.is_clean](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults.is_clean):

In [3]:
if results.is_clean:
    print("DRC passed!\n")
else:
    print("DRC did not pass!\n")

DRC did not pass!



A summary of DRC violations can be printed:

In [4]:
print(results)

DRC results summary
--------------------------------
Total violations: 3

Violations by category:
min_width: 2
min_gap: 0
min_area: 1
min_hole: 0



The names of all the checked categories can be retrieved with [DRCResults.categories](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults.categories)

In [5]:
results.categories

('min_width', 'min_gap', 'min_area', 'min_hole')

To get the markers for a specific category, index [DRCResults](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults) by key:

In [6]:
# This will show how many violation shapes were found for the 'min_width' rule.
print(results["min_width"].count)

# This will show all of the violation marker shapes for the 'min_width' rule
print(results["min_width"].markers)

2
(EdgePairMarker(attrs={}, edge_pair=(((-1.717, -0.141), (-2.0, 0.0)), ((-2.0, 0.0), (-1.776, 0.224))), type='EdgePairMarker'), EdgePairMarker(attrs={}, edge_pair=(((2.0, 0.0), (1.717, -0.141)), ((1.776, 0.224), (2.0, 0.0))), type='EdgePairMarker'))


Results can also be loaded from a KLayout DRC database file with [DRCResults.load(resultsfile)](https://docs.flexcompute.com/projects/tidy3d/en/latest/api/_autosummary/tidy3d.plugins.klayout.drc.html#tidy3d.plugins.klayout.drc.DRCResults.load)

In [7]:
print(DRCResults.load("drc_results.lyrdb"))

DRC results summary
--------------------------------
Total violations: 3

Violations by category:
min_width: 2
min_gap: 0
min_area: 1
min_hole: 0

